Making Change
----------------------

Consider the classic problem of making change.  Your currency has `k` denominations of bills.  You would like to produce a combination of them (each denomination can be picked zero or more times) with a value `amount`, which is at most `C`.  Find the combination with the fewest bills.

In [ ]:
import random

In [ ]:
def change_size_recursive(denominations, amount):
    """Find the smallest number of bills required to make change
    for amount, if each bill is one of the given denominations.
    
    Input:
        denominations: a list of integer bill sizes (e.g., [2,3,13])
        amount: the amount you want to make change for
    
    Output:
        A single integer, the fewest bills possible to make exact change of size amount.
        If no solution is possible, return None.
    """
    def f(amount):
        if amount == 0:
            return 0
        if amount < 0:
            return None
        best_option = None
        for bill in denominations:
            option = f(XXX_FIX_ME)
            if option is not None:
                if best_option is None or option < best_option:
                    best_option = option + 1
        return best_option
    return f(amount)

In [ ]:
denominations1 = [1, 2, 5, 10, 20, 50, 100]
print(change_size_recursive(denominations1, 16)) #3

denominations2 = [5, 9, 13, 17]
print(change_size_recursive(denominations2, 14)) #2
print(change_size_recursive(denominations2, 16)) #None
print(change_size_recursive(denominations2, 26)) #2

%timeit change_size_recursive(denominations1, 26)
#This is already getting sluggish with amount=26...




Questions
------------

(a) In the code above, what does `f(t)` represent?

(b) What is the running time for `change_size_recursive`?


In [ ]:
# Let's try the same `memoize` as pset 1
# (slightly modified to work with mutable inputs/outputs)
import functools
import pickle

def memoize(f):
    """This can turn any recursive function into a memoized version.
    
    We use pickle.dumps/pickle.loads to deal with mutable inputs/outputs.
    If the function returns a list, we don't want a subsequent modification
    (e.g., result.append(1)) to corrupt the cached value.
    """
    cache = {}
    @functools.wraps(f)
    def wrap(*args):
        args_hash = pickle.dumps(args)
        if args_hash not in cache:
            cache[args_hash] = pickle.dumps(f(*args))  
        return pickle.loads(cache[args_hash])
    wrap.cache = cache                #so we can clear it as needed
    return wrap

In [ ]:
#The code is exactly the same as change_size_recursive, but with @memoize.
def change_size_memoized(denominations, amount):
    """Find the smallest number of bills required to make change
    for amount, if each bill is one of the given denominations.
    
    Input:
        denominations: a list of integer bill sizes (e.g., [2,3,13])
        amount: the amount you want to make change for
    
    Output:
        A single integer, the fewest bills possible to make exact change of size amount.
        If no solution is possible, return None.
    """
    @memoize
    def f(amount):
        if amount == 0:
            return 0
        if amount < 0:
            return None
        best_option = None
        for bill in denominations:
            option = f(XXX_FIX_ME_AS_BEFORE)
            if option is not None:
                if best_option is None or option < best_option:
                    best_option = option + 1
        return best_option
    return f(amount)

In [ ]:
denominations1 = [1, 2, 5, 10, 20, 50, 100]
print(change_size_memoized(denominations1, 16)) #3
print(change_size_memoized(denominations1, 26)) #3
print(change_size_memoized(denominations1, 406)) #6

denominations2 = [5, 9, 13, 17]
print(change_size_memoized(denominations2, 14)) #2
print(change_size_memoized(denominations2, 16)) #None
print(change_size_memoized(denominations2, 1006)) #62

denominations3 = random.sample(range(100, 200), 10)

%timeit change_size_memoized(denominations1, 26)
%timeit change_size_memoized(denominations1, 406)
%timeit change_size_memoized(denominations3, 4006)
%timeit change_size_memoized(denominations3, 40006)

Questions
------------

(c) What is the asymptotic running time for `change_size_memoized`?

Finding the set
=================

The above algorithms find the _size_ of the optimal solution.  How can we find the actual solution?

In [ ]:
# Here's one way: we modify change_set_memoized a bit.

def change_set_memoized(denominations, amount):
    """Find the smallest number of bills required to make change
    for amount, if each bill is one of the given denominations.
    
    Input:
        denominations: a list of integer bill sizes (e.g., [2,3,13])
        amount: the amount you want to make change for
    
    Output:
        A list of bill values, the shortest possible such list with sum `amount`.
        If no solution is possible, return None.
    """
    @memoize
    def f(amount):
        if amount == 0:
            return []
        if amount < 0:
            return None
        best_option = None
        for bill in denominations:
            option = f(XXX_FIX_ME_AS_BEFORE)
            if option is not None:
                if best_option is None or len(option) < len(best_option):
                    best_option = YYY_MAKE_ME_WORK
        return best_option
    return f(amount)

In [ ]:
print(change_set_memoized(denominations1, 16))   # [1, 5, 10]
print(change_set_memoized(denominations1, 406))  # [1, 5, 100, 100, 100, 100]

print(change_set_memoized(denominations2, 14))   # [5, 9]
print(change_set_memoized(denominations2, 16))   # None
print(change_set_memoized(denominations2, 1006)) # [5, 5, 5, 5, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17]

%timeit change_set_memoized(denominations1, 406)
%timeit change_set_memoized(denominations3, 4006)
%timeit change_set_memoized(denominations3, 40006)

Questions
------------


(d) What is the asymptotic running time for `change_set_memoized`?

(Hint: it is worse than `change_size_memoized`.)


Bottom-up dynamic programming
=======

Rather than do recursion with memoization, we can build the solution from the bottom up.

In [ ]:
# As you can see, this is essentially the same
# code as in `change_size_recursive` and all the other
# versions, just run in a different order.
def change_bottomup_size(denominations, amount):
    best = [None]*(amount+1)
    best[0] = 0
    for i in range(1, amount+1):
        best_option = None
        for bill in denominations:
            if bill <= i and best[i-bill] is not None:
                option = best[i-bill] + XXX_FIX_ME
                if best_option is None or option < best_option:
                    best_option = option
        best[i] = best_option
    return best[amount]



In [ ]:
denominations1 = [1, 2, 5, 10, 20, 50, 100]
print(change_bottomup_size(denominations1, 16)) #3
print(change_bottomup_size(denominations1, 406)) #6

denominations2 = [5, 9, 13, 17]
print(change_bottomup_size(denominations2, 14)) #2
print(change_bottomup_size(denominations2, 16)) #None
print(change_bottomup_size(denominations2, 1006)) #62

%timeit change_bottomup_size(denominations1, 406)
%timeit change_bottomup_size(denominations3, 4006)
%timeit change_bottomup_size(denominations3, 40006)

Questions
------------


(e) What is the asymptotic running time for `change_bottomup_size`?

(f) How does the empirical performance compare to `change_size_memoized`?  Why?

Finding the set
=================

There is a simple way to extend `change_bottomup_size` to also generate the optimal set: when constructing the table, also create a list of _back pointers_ saying which choice was made to generate a given value.

We can then find the solution by walking the path back from `amount` to zero.

In [ ]:
def change_bottomup_set(denominations, amount):
    best = [None]*(amount+1)
    best[0] = 0
    back = [None]*(amount+1)                   # new line
    for i in range(1, amount+1):
        best_option = None
        for bill in denominations:
            if bill <= i and best[i-bill] is not None:
                option = best[i-bill] + XXX_FIX_ME_AS_BEFORE
                if best_option is None or option < best_option:
                    best_option = option
                    back[i] = bill             # new line
        best[i] = best_option
        
    # Now that we have the back[] array, produce the answer.
    if best[amount] is None:
        return None
    answer = []
    remaining = amount
    while remaining:
        answer.append(back[remaining])
        remaining -= XXX_SOMETHING
    return answer


In [ ]:
denominations1 = [1, 2, 5, 10, 20, 50, 100]
print(change_bottomup_set(denominations1, 16)) #[1, 5, 10]
print(change_bottomup_set(denominations1, 406)) # [1, 5, 100, 100, 100, 100]

denominations2 = [5, 9, 13, 17]
print(change_bottomup_set(denominations2, 14)) # [5, 9]
print(change_bottomup_set(denominations2, 16)) # None
print(change_bottomup_set(denominations2, 1006)) # [5, 5, 5, 5, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17, 17]

%timeit change_bottomup_set(denominations1, 406)
%timeit change_bottomup_set(denominations3, 4006)
%timeit change_bottomup_set(denominations3, 40006)

Questions
------------

(g) What is the asymptotic running time for `change_bottomup_set`?

